In [1]:
# Run some setup code for this notebook.

import random
import numpy as np
from scipy.optimize import minimize
'''import matplotlib.pyplot as plt
import statsmodels.api as sm

from bokeh.io import push_notebook, show, output_notebook
from bokeh.plotting import figure
from bokeh.layouts import gridplot
output_notebook()

%matplotlib inline

#plt.rcParams['image.interpolation'] = 'nearest'
#plt.rcParams['image.cmap'] = 'gray'

# Some more magic so that the notebook will reload external python modules;
# see http://stackoverflow.com/questions/1907993/autoreload-of-modules-in-ipython
#%load_ext autoreload
#%autoreload 2'''

"import matplotlib.pyplot as plt\nimport statsmodels.api as sm\n\nfrom bokeh.io import push_notebook, show, output_notebook\nfrom bokeh.plotting import figure\nfrom bokeh.layouts import gridplot\noutput_notebook()\n\n%matplotlib inline\n\n#plt.rcParams['image.interpolation'] = 'nearest'\n#plt.rcParams['image.cmap'] = 'gray'\n\n# Some more magic so that the notebook will reload external python modules;\n# see http://stackoverflow.com/questions/1907993/autoreload-of-modules-in-ipython\n#%load_ext autoreload\n#%autoreload 2"

In [2]:
n=100000 # size of training dataset
k_1=4 #the number of random columns of x, so k is the number of parameters to estimate
#x = np.concatenate((np.ones((n,1)),np.random.random_sample((n, k_1))*10-5),axis=1)#old version

#create explanatory, independent variables
xwide=1
spreadx=np.random.randint(xwide, size=(1,k_1))+1#random row vector to multiply by each random column of x to allow s.d. upto 5
xtall=1
shiftx=np.random.randint(0,xtall, size=(1,k_1))-xtall/2#random row vector to add to each column of x
randx=np.random.randn(n,k_1)
x = np.concatenate((np.ones((n,1)),shiftx+spreadx*randx),axis=1)

#generate error~N(0,1)
e=np.random.randn(n)*1
e2=np.square(e)

#make beta integer, non-zero
Beta=(np.random.randint(10, size=(k_1+1,))+1)*(2*np.random.randint(2, size=(k_1+1,))-np.ones(k_1+1,)) #if beta is a random integer, it could be 0
#make a simple y for testing
y=np.matmul(x, Beta)+e
'''
plt.subplot(221)
plt.scatter(x[:,1],y,s=6, c=e2)
plt.xlabel(str(Beta[1]))
plt.subplot(222)
plt.scatter(x[:,2],y,s=6, c=e2)
plt.xlabel(str(Beta[2]))
plt.subplot(223)
plt.scatter(x[:,3],y,s=6, c=e2)
plt.xlabel(str(Beta[3]))
plt.subplot(224)
plt.scatter(x[:,4],y,s=6, c=e2)
plt.xlabel(str(Beta[4]))
plt.show()

print (Beta)
print(spreadx)
print(shiftx)'''

'\nplt.subplot(221)\nplt.scatter(x[:,1],y,s=6, c=e2)\nplt.xlabel(str(Beta[1]))\nplt.subplot(222)\nplt.scatter(x[:,2],y,s=6, c=e2)\nplt.xlabel(str(Beta[2]))\nplt.subplot(223)\nplt.scatter(x[:,3],y,s=6, c=e2)\nplt.xlabel(str(Beta[3]))\nplt.subplot(224)\nplt.scatter(x[:,4],y,s=6, c=e2)\nplt.xlabel(str(Beta[4]))\nplt.show()\n\nprint (Beta)\nprint(spreadx)\nprint(shiftx)'

In [3]:


def myreg(y,x):
    # a simple regression that prints its own mse and returns estimated parameters
    q=np.linalg.inv(np.matmul(x.T,x))
    bhat=np.matmul(np.matmul(q,x.T),y)
    mse=np.sum((y-x@bhat)**2)/y.shape[0]
    #print('mse=',mse)
    return bhat

def myreg_mse(y,x):
    # a simple regression that prints its own mse and returns estimated parameters
    q=np.linalg.inv(np.matmul(x.T,x))
    bhat=np.matmul(np.matmul(q,x.T),y)
    mse=np.sum((y-x@bhat)**2)/y.shape[0]
    return mse



def myregstdz(y,x): 
    [n,k]=np.shape(x)
    onecol=0
    xfull=x
    if np.allclose(np.ones([n,1]),x[:,0]):#fix problems with standardizing column of 1's
        x=x[:,1:]
        onecol=1;
    xmean=np.mean(x,axis=0)
    xvar=np.var(x,axis=0,ddof=1)#subtracting xmean isn't necessary, as it happens anyways
    onevec=np.ones([n,1])
    yvar=np.var(y, ddof=1)
    sy=np.power(yvar,.5)
    sx=np.power(xvar,.5)
    ymean=np.mean(y)        
    xstdz=(1/sx)*(x-xmean)
    ystdz=(1/sy)*(y-ymean)
    Q=np.linalg.inv(np.matmul(xstdz.T,xstdz))
    bhat1=np.matmul(np.matmul(Q,xstdz.T),ystdz)
    bhat=sy*bhat1*(1/sx)#undo beta coef. by multiplying each by Sy/Sx
    print(sy)
    print(xmean)
    if onecol==1:
        bhat_int=ymean-np.sum(sy*xmean*bhat1*(1/sx))
        bhat=np.concatenate([[bhat_int],bhat])
    mse=np.sum((y-xfull@bhat)**2)/y.shape[0]
    print('mse=',mse)
    return bhat

def myPLWLS(y,x,attr1=x,mse=1,costfn=1):
    print('mse=',mse,'costfn=',costfn)
    if np.allclose(np.ones([attr1.shape[0],]),attr1[:,0]):#fix problems with differencing column of 1's
        attr=attr1[:,1:]
    else: attr=attr1
    n,k=np.shape(x)
    j=np.shape(attr)[1]+1 #plus 1 to go with the column of 1's added after differencing
    attr_tile=np.tile(attr,(n,1,1))# stack the attributes matrix (nxk array) n times
    diffstack=np.transpose(attr_tile,(1,0,2))-attr_tile#transpose the z and x dimensions (listed as z,x,y)
    diffstack=np.concatenate((np.ones([n,n,1]),diffstack), axis=2) # add a column of 1's to all the differences
    wt_try0=np.zeros([j,])
    wt_try0[0]=1
    return minimize(PLWLStryMSE,wt_try0,args=(y,x,diffstack,mse,costfn),method='Nelder-Mead')

def Attr_To_Diffstck(attr):
    n,j=np.shape(attr); j+=1 #plus 1 to go with the column of 1's added after differencing
    attr_tile=np.tile(attr,(n,1,1))# stack the attributes matrix (nxk array) n times
    diffstack=np.transpose(attr_tile,(1,0,2))-attr_tile#transpose the z and x dimensions (listed as z,x,y)
    return np.concatenate((np.ones([n,n,1]),diffstack), axis=2)


def Reg_wts_stack(corrparams,diffstack):
    #return np.sum(((2**corrparams*diffstack)**2),axis=2)**-0.5)
    #weighted, squared, summed across wt parameter, j, rooted and flipped
    regwt_stack=np.sum(np.exp((corrparams*diffstack)**2),axis=2)**(-0.5)
    return regwt_stack/(np.sum(regwt_stack**2)**.5/regwt_stack.shape[0])#normalize the weights seems to help convergence
    
def PLWLScastMSE(corrparams,attr1,y,x):
    #use corrparams, correspondence attributes, known y and x to calculate mse for the estimator/corrparams
    if np.allclose(np.ones([attr1.shape[0],]),attr1[:,0]):#fix problems with differencing column of 1's
        attr=attr1[:,1:]
    else: attr=attr1
    n,k=np.shape(x)
    regwt_stack=Reg_wts_stack(corrparams,Attr_To_Diffstck(attr))
    
    x_wt_stck=np.tile(regwt_stack.reshape(n,n,1),(1,1,k))*np.tile(x,(n,1,1))
    y_wt_stck=regwt_stack.reshape(n,n,1)*np.tile(y.reshape(n,1),(n,1,1))
    x_wt_stckT=np.transpose(x_wt_stck,(0,2,1))#transpose X aross the stack for x'x
    Qi=np.linalg.inv(x_wt_stckT@x_wt_stck)
    Bstack=Qi@x_wt_stckT@y_wt_stck
    #print('first 5 params=',Bstack[0:5,:,:])
    
                             
    ystack=np.tile(y.reshape(n,1),(n,1,1))
    xstack=np.tile(x,(n,1,1))
    err=(ystack-xstack@Bstack)#errors are not calculated using weighted y and x
    
    yhat_stack=xstack@Bstack                         
    yhats=yhat_stack.diagonal().diagonal()
    err_diag=err.diagonal().diagonal()
    mse=np.sum(err_diag**2)/err_diag.size
    '''p=figure()
    p.circle(x[:,1],y)
    p.square(x[:,1],yhats)
    p.show()'''
    #print('mse_cast=',mse)
    return mse
    

    
def PLWLStryMSE(corrparams,y,x,diffstack,MSE=1,costfn=1):
    #print(x.shape)
    print('corrparams=',corrparams)
    n,k=np.shape(x)
    j=np.shape(corrparams)[0]
    #print(k,j)
    regwt_stack=Reg_wts_stack(corrparams,diffstack)
    x_wt_stck=np.tile(regwt_stack.reshape(n,n,1),(1,1,k))*np.tile(x,(n,1,1))#the stack of weights is broadcast and multiplied by stack of x.(z,x,y) indexing
    y_wt_stck=regwt_stack.reshape(n,n,1)*np.tile(y.reshape(n,1),(n,1,1))#the stack of weights is broadcast and multiplied by stack of y.
    x_wt_stckT=np.transpose(x_wt_stck,(0,2,1))#transpose X aross the stack
    Qi=np.linalg.inv(x_wt_stckT@x_wt_stck)
    #print(y_wt_stck.shape)
    Bstack=Qi@x_wt_stckT@y_wt_stck #use weighted data to calculate gls parameters
    #print('first params=',Bstack[0,:,:])
    ystack=np.tile(y.reshape(n,1),(n,1,1))
    xstack=np.tile(x,(n,1,1))
    err=(ystack-xstack@Bstack)#errors are not calculated using weighted y and x
    if costfn==1: cost_err=err**2-regwt_stack**(-2) #squared error prediction
    if costfn==2: cost_err=err
    corr_err=err**2-regwt_stack**(-2)
    if MSE==1:
        out=np.sum(cost_err**2)/cost_err.size
        print('{}MSE all='.format(costfn),out)
        return out
    if MSE==2:
        wt_cost_err=(cost_err)*regwt_stack
        out=np.sum(wt_cost_err**2)/wt_cost_err.size
        print('{}MSE wt_all='.format(costfn),out)
        return out
    if MSE==3:
        diag_err=cost_err.diagonal().diagonal()
        print('diag',diag_err.shape)
        out=np.sum(diag_err**2)/diag_err.size
        print('{}MSE n_only='.format(costfn),out)
        return out
    





In [4]:
def PLWLSpredict(corrparams,attr1,y,x,attr1_val,y_val,x_val):
    #use corrparams, correspondence attributes, known y and x to calculate mse for the estimator/corrparams
    if np.allclose(np.ones([attr1.shape[0],]),attr1[:,0]):#fix problems with differencing column of 1's
        attr=attr1[:,1:]
    else: attr=attr1
    if np.allclose(np.ones([attr1_val.shape[0],]),attr1_val[:,0]):#fix problems with differencing column of 1's
        attr_val=attr1_val[:,1:]    
    else: attr_val=attr1_val
    n,k=np.shape(x)
    nv,k1=np.shape(x_val)
    j=np.shape(attr)[1]+1 #plus 1 to go with the column of 1's added after differencing
    ctr_attr_stck=np.tile(attr_val,(n,1,1))# stack the centered attributes matrix (nxk array) n times
    diffstack0=np.transpose(ctr_attr_stck,(1,0,2))-np.tile(attr,(nv,1,1))#transpose the z and x dimensions (listed as z,x,y)
    diffstack=np.concatenate((np.ones([nv,n,1]),diffstack0), axis=2) ##so diffstack is shape nv,n,j
    
    regwt_stack=Reg_wts_stack(corrparams,diffstack)
    x_wt_stck=np.tile(regwt_stack.reshape(nv,n,1),(1,1,k))*np.tile(x,(nv,1,1))
    y_wt_stck=regwt_stack.reshape(nv,n,1)*np.tile(y.reshape(n,1),(nv,1,1))
    x_wt_stckT=np.transpose(x_wt_stck,(0,2,1))#transpose X aross the stack for x'x
    Qi=np.linalg.inv(x_wt_stckT@x_wt_stck)
    Bstack=Qi@x_wt_stckT@y_wt_stck
    #print('first 5 params=',Bstack[0:5,:,:])
                                 
    ystack=np.tile(y_val.reshape(nv,1),(nv,1,1))
    xstack=np.tile(x_val,(nv,1,1))
    err=(ystack-xstack@Bstack)#errors are not calculated using weighted y and x
    
    yhat_stack=xstack@Bstack                         
    yhats=yhat_stack.diagonal().diagonal()
    err_diag=err.diagonal().diagonal()
    mse=np.sum(err_diag**2)/err_diag.size
    '''p=figure()
    p.circle(x[:,1],y)
    p.square(x[:,1],yhats)
    p.show()'''
    #print('mse_cast=',mse)
    return mse    

def myregpredict(y,x,yval,xval):
    # a simple regression that prints its own mse and returns estimated parameters
    q=np.linalg.inv(np.matmul(x.T,x))
    bhat=np.matmul(np.matmul(q,x.T),y)
    mse=np.sum((yval-xval@bhat)**2)/yval.shape[0]
    #print('mse=',mse)
    return mse

In [ ]:
nj=200
j=np.random.randint(nj, size=(nj,))
xi=x[j,:]
yi=y[j]

#def MonteYquad()
y2=x[:,0]*Beta[0]+x[:,1]*Beta[1]+x[:,1]**2*Beta[2]+np.random.randn(n)*1
x2=x[:,0:2]
yi2=y2[j]
xi2=x2[j,:]
print(yi2.shape,xi2.shape)
print(Beta)
print(myreg(yi2,xi2))
print(myregstdz(yi2,xi2))
attr=xi2
corrmodel_list=[myPLWLS(yi2,xi2,attr,j+1,i+1) for i in range(2) for j in range(2)]
#print(corrmodel_list)



(200,) (200, 2)
[ -8.  -4.  -2.  -4. -10.]
[-9.95820814 -3.0653432 ]
4.213027254535697
[-0.42128595]
mse= 8.559259973125934
[-9.95820814 -3.0653432 ]
mse= 1 costfn= 1
corrparams= [1. 0.]
1MSE all= 437.27439979348674
corrparams= [1.05 0.  ]
1MSE all= 437.27439979348696
corrparams= [1.0e+00 2.5e-04]
1MSE all= 437.27441846328134
corrparams= [ 1.05e+00 -2.50e-04]
1MSE all= 437.2744170978219
corrparams= [ 1.0375e+00 -1.2500e-04]
1MSE all= 437.27440420486636
corrparams= [1.0125e+00 1.2500e-04]
1MSE all= 437.27440437559653
corrparams= [ 1.03125e+00 -6.25000e-05]
1MSE all= 437.2744009069988
corrparams= [1.01875e+00 6.25000e-05]
1MSE all= 437.274400928342
corrparams= [ 1.028125e+00 -3.125000e-05]
1MSE all= 437.27440007319797
corrparams= [1.021875e+00 3.125000e-05]
1MSE all= 437.2744000758659
corrparams= [ 1.0265625e+00 -1.5625000e-05]
1MSE all= 437.27439986358127
corrparams= [1.0234375e+00 1.5625000e-05]
1MSE all= 437.2743998639142
corrparams= [ 1.02578125e+00 -7.81250000e-06]
1MSE all= 437.274

1MSE wt_all= 437.0389739118865
corrparams= [0.00786133 0.02035297]
1MSE wt_all= 436.9986737620812
corrparams= [-0.06141357  0.02398094]
1MSE wt_all= 436.89244804147415
corrparams= [0.7005249  0.03027046]
1MSE wt_all= 436.81069532814087
corrparams= [1.20270386 0.03861558]
1MSE wt_all= 436.893603452079
corrparams= [0.18100586 0.03438165]
1MSE wt_all= 436.5015408395983
corrparams= [0.04245605 0.0416376 ]
1MSE wt_all= 436.12463082194745
corrparams= [0.80439453 0.04792712]
1MSE wt_all= 436.22040764458046
corrparams= [0.14632568 0.05929427]
1MSE wt_all= 434.9740115080784
corrparams= [-0.13077393  0.07380617]
1MSE wt_all= 433.7185846643613
corrparams= [-0.8927124   0.06751665]
1MSE wt_all= 435.37447435022614
corrparams= [-1.06594238  0.09968521]
1MSE wt_all= 433.96912325350837
corrparams= [-0.30400391  0.10597473]
1MSE wt_all= 430.2990252879572
corrparams= [-0.00964966  0.12520377]
1MSE wt_all= 427.25995979205726
corrparams= [0.9255188  0.09932473]
1MSE wt_all= 433.2946135325073
corrparams= [

2MSE all= 8.559259973125933
corrparams= [ 1.04996948e+00 -1.83105469e-07]
2MSE all= 8.559259973125934
corrparams= [1.04982758e+00 1.37329102e-07]
2MSE all= 8.559259973125934
corrparams= [1.04987488e+00 3.05175781e-08]
2MSE all= 8.559259973125934
corrparams= [1.04989014e+00 1.22070313e-07]
2MSE all= 8.559259973125933
corrparams= [1.05001526e+00 9.15527344e-08]
2MSE all= 8.559259973125934
corrparams= [1.04990997e+00 4.57763672e-08]
2MSE all= 8.559259973125934
corrparams= [1.04994507e+00 6.10351563e-08]
2MSE all= 8.559259973125933
corrparams= [1.04993744e+00 1.52587891e-08]
2MSE all= 8.559259973125934
mse= 2 costfn= 2
corrparams= [1. 0.]
2MSE wt_all= 8.559259973125942
corrparams= [1.05 0.  ]
2MSE wt_all= 8.559259973125936
corrparams= [1.0e+00 2.5e-04]
2MSE wt_all= 8.55925963040965
corrparams= [1.05e+00 2.50e-04]
2MSE wt_all= 8.559259655475007
corrparams= [1.e+00 5.e-04]
2MSE wt_all= 8.559258602260062
corrparams= [9.75e-01 7.50e-04]
2MSE wt_all= 8.559256776076955
corrparams= [9.25e-01 7.50

2MSE wt_all= 7.461040929352785
corrparams= [-8.77143569e-05  4.40570621e-01]
2MSE wt_all= 7.4610409225334156
corrparams= [-3.21491626e-05  4.40557663e-01]
2MSE wt_all= 7.461040921260678
corrparams= [1.10755002e-04 4.40551798e-01]
2MSE wt_all= 7.461040924110332
corrparams= [-3.80970172e-05  4.40565915e-01]
2MSE wt_all= 7.461040920993102


In [ ]:
corrparam_list=[corrmodel_list[i].x for i in range(4)]
print(corrparam_list)
corrparam_MSE_list=[corrmodel_list[i].fun for i in range(4)]
print(corrparam_MSE_list)

[array([ 1.03900488e+00, -1.18996366e-07]), array([-3.30438960e-05,  2.96839758e-01]), array([1.05, 0.  ]), array([-3.80970172e-05,  4.40565915e-01])]
[437.2743997934856, 403.3051037021529, 8.559259973125933, 7.461040920993102]


In [ ]:
'''predict boot needs to take in a list of functions to try
it also needs to probably take the out-of-bootstrap approach, which likely means separating the data
I may need to go back and redo these to explicitly avoid data leaking between training and validation
rather than just randomly sampling. i don't think it should matter since n is big.'''
m=500
def predict_boot(corrparam_try):
    nj_val=nj+1 #different size possible
    MSElist=np.empty([m,len(corrparam_try),4])
    for i in range(m):
        j=np.random.randint(nj, size=(nj,))
        yi2=y2[j]; xi2=x2[j]
        jv=np.random.randint(nj_val, size=(nj_val,))
        yi2v=y2[jv]; xi2v=x2[jv]
        for k in range(len(corrparam_try)):
            MSElist[i,k,0]=PLWLScastMSE(corrparam_try[k],xi2,yi2,xi2)
            MSElist[i,k,1]=PLWLSpredict(corrparam_try[k],xi2,yi2,xi2,xi2v,yi2v,xi2v)
            MSElist[i,k,2]=myregpredict(yi2,xi2,yi2v,xi2v)
            MSElist[i,k,3]=myreg_mse(yi2v,xi2v)
    return MSElist
print(np.sum(predict_boot(corrparam_list),axis=0))

'''m=500
def predict_boot2(corrparam_try):
    nj_val=nj+1
    MSElist=np.empty([m,len(corrparam_try),4])
    for i in range(m):
        j=np.random.randint(nj, size=(nj,))
        yi2=y2[j]; xi2=x2[j]
        jv=np.random.randint(nj_val, size=(nj_val,))
        yi2v=y2[jv]; xi2v=x2[jv]
        for k in range(len(corrparam_try)):
            MSElist[i,k,0]=PLWLScastMSE(corrparam_try[k],xi2,yi2,xi2)
            MSElist[i,k,1]=PLWLSpredict(corrparam_try[k],xi2,yi2,xi2,xi2v,yi2v,xi2v)
            MSElist[i,k,2]=myregpredict(yi2,xi2,yi2v,xi2v)
            MSElist[i,k,3]=myreg_mse(yi2v,xi2v)
    return MSElist'''


[[3406.3792687  3191.61840085 3663.84039999 3484.96066687]
 [2490.78388243 2387.20588111 3663.84039999 3484.96066687]
 [3406.3792687  3191.61840085 3663.84039999 3484.96066687]
 [1711.48532626 1673.04584668 3663.84039999 3484.96066687]]


'm=500\ndef predict_boot2(corrparam_try):\n    nj_val=nj+1\n    MSElist=np.empty([m,len(corrparam_try),4])\n    for i in range(m):\n        j=np.random.randint(nj, size=(nj,))\n        yi2=y2[j]; xi2=x2[j]\n        jv=np.random.randint(nj_val, size=(nj_val,))\n        yi2v=y2[jv]; xi2v=x2[jv]\n        for k in range(len(corrparam_try)):\n            MSElist[i,k,0]=PLWLScastMSE(corrparam_try[k],xi2,yi2,xi2)\n            MSElist[i,k,1]=PLWLSpredict(corrparam_try[k],xi2,yi2,xi2,xi2v,yi2v,xi2v)\n            MSElist[i,k,2]=myregpredict(yi2,xi2,yi2v,xi2v)\n            MSElist[i,k,3]=myreg_mse(yi2v,xi2v)\n    return MSElist'

In [ ]:
ii=500
n1=200
corrparam_list2=[]
for i in range(ii):
    print(i)
    j=np.random.randint(n1, size=(n1,))
    corrparam_list2.append(myPLWLS(y2[j],x2[j],x2[j],2,2).x)
print(np.sum(predict_boot(corrparam_list2),axis=0))


0
mse= 2 costfn= 2
corrparams= [1. 0.]
2MSE wt_all= 4.564024895852367
corrparams= [1.05 0.  ]
2MSE wt_all= 4.564024895852367
corrparams= [1.0e+00 2.5e-04]
2MSE wt_all= 4.5640247493249015
corrparams= [9.5e-01 2.5e-04]
2MSE wt_all= 4.564024738648627
corrparams= [9.00e-01 3.75e-04]
2MSE wt_all= 4.564024518419081
corrparams= [9.00e-01 6.25e-04]
2MSE wt_all= 4.564023847426014
corrparams= [0.85      0.0009375]
2MSE wt_all= 4.5640223916850955
corrparams= [0.75      0.0010625]
2MSE wt_all= 4.564021323866773
corrparams= [0.625      0.00146875]
2MSE wt_all= 4.564017306693075
corrparams= [0.575      0.00203125]
2MSE wt_all= 4.564009858260466
corrparams= [0.4125     0.00285937]
2MSE wt_all= 4.563992283857123
corrparams= [0.1875     0.00339063]
2MSE wt_all= 4.563975667880841
corrparams= [-0.14375     0.00461719]
2MSE wt_all= 4.563932935633742
corrparams= [-0.35625     0.00600781]
2MSE wt_all= 4.563877541943233
corrparams= [-0.846875    0.00827734]
2MSE wt_all= 4.563828962700399
corrparams= [-1.4031

2MSE wt_all= 3.8234645705190635
corrparams= [-2.67200478e-04  5.57228041e-01]
2MSE wt_all= 3.8234645743644946
corrparams= [2.35987115e-05 5.57238570e-01]
2MSE wt_all= 3.8234645710336865
1
mse= 2 costfn= 2
corrparams= [1. 0.]
2MSE wt_all= 7.104804100919563
corrparams= [1.05 0.  ]
2MSE wt_all= 7.10480410091956
corrparams= [1.0e+00 2.5e-04]
2MSE wt_all= 7.104803821666496
corrparams= [1.05e+00 2.50e-04]
2MSE wt_all= 7.1048038420903294
corrparams= [1.e+00 5.e-04]
2MSE wt_all= 7.104802983906758
corrparams= [9.75e-01 7.50e-04]
2MSE wt_all= 7.104801495891354
corrparams= [9.25e-01 7.50e-04]
2MSE wt_all= 7.104801313708528
corrparams= [0.8625 0.001 ]
2MSE wt_all= 7.1047987488723985
corrparams= [0.8375 0.0015]
2MSE wt_all= 7.104791709278978
corrparams= [0.75625  0.002125]
2MSE wt_all= 7.104777033794366
corrparams= [0.64375  0.002375]
2MSE wt_all= 7.104766817610511
corrparams= [0.478125  0.0031875]
2MSE wt_all= 7.104729307624191
corrparams= [0.371875  0.0043125]
2MSE wt_all= 7.104660278629094
corrp

2MSE wt_all= 5.91695728531821
corrparams= [2.48294670e-05 5.36270384e-01]
2MSE wt_all= 5.916957284448122
2
mse= 2 costfn= 2
corrparams= [1. 0.]
2MSE wt_all= 5.825489434072576
corrparams= [1.05 0.  ]
2MSE wt_all= 5.825489434072575
corrparams= [1.0e+00 2.5e-04]
2MSE wt_all= 5.825489257112856
corrparams= [1.05e+00 2.50e-04]
2MSE wt_all= 5.825489270055217
corrparams= [1.e+00 5.e-04]
2MSE wt_all= 5.825488726233366
corrparams= [9.75e-01 7.50e-04]
2MSE wt_all= 5.825487783293891
corrparams= [9.25e-01 7.50e-04]
2MSE wt_all= 5.82548766784659
corrparams= [0.8625 0.001 ]
2MSE wt_all= 5.825486042537632
corrparams= [0.8375 0.0015]
2MSE wt_all= 5.825481581625498
corrparams= [0.75625  0.002125]
2MSE wt_all= 5.825472281941928
corrparams= [0.64375  0.002375]
2MSE wt_all= 5.825465808067795
corrparams= [0.478125  0.0031875]
2MSE wt_all= 5.825442038470584
corrparams= [0.371875  0.0043125]
2MSE wt_all= 5.825398295818065
corrparams= [0.1265625  0.00596875]
2MSE wt_all= 5.825303404602174
corrparams= [-0.15156

2MSE wt_all= 6.973364683456157
corrparams= [1.e+00 5.e-04]
2MSE wt_all= 6.973363515153667
corrparams= [9.75e-01 7.50e-04]
2MSE wt_all= 6.9733614894187115
corrparams= [9.25e-01 7.50e-04]
2MSE wt_all= 6.97336124140113
corrparams= [0.8625 0.001 ]
2MSE wt_all= 6.973357749717331
corrparams= [0.8375 0.0015]
2MSE wt_all= 6.973348166239626
corrparams= [0.75625  0.002125]
2MSE wt_all= 6.973328187484812
corrparams= [0.64375  0.002375]
2MSE wt_all= 6.973314279486065
corrparams= [0.478125  0.0031875]
2MSE wt_all= 6.9732632144789894
corrparams= [0.371875  0.0043125]
2MSE wt_all= 6.973169240169688
corrparams= [0.1265625  0.00596875]
2MSE wt_all= 6.972965379345854
corrparams= [-0.1515625   0.00703125]
2MSE wt_all= 6.972812368556488
corrparams= [-0.60546875  0.00948438]
2MSE wt_all= 6.972532085238223
corrparams= [-0.95703125  0.01226563]
2MSE wt_all= 6.972392175012865
corrparams= [-1.67460938  0.01680469]
2MSE wt_all= 6.972999833129178
corrparams= [-1.6890625   0.01578125]
2MSE wt_all= 6.9730574651716

2MSE wt_all= 6.508462787292072
corrparams= [0.8625 0.001 ]
2MSE wt_all= 6.508459969434994
corrparams= [0.8375 0.0015]
2MSE wt_all= 6.508452235379885
corrparams= [0.75625  0.002125]
2MSE wt_all= 6.508436112128161
corrparams= [0.64375  0.002375]
2MSE wt_all= 6.508424888097859
corrparams= [0.478125  0.0031875]
2MSE wt_all= 6.508383677616127
corrparams= [0.371875  0.0043125]
2MSE wt_all= 6.5083078384336135
corrparams= [0.1265625  0.00596875]
2MSE wt_all= 6.508143318525775
corrparams= [-0.1515625   0.00703125]
2MSE wt_all= 6.508019835470815
corrparams= [-0.60546875  0.00948438]
2MSE wt_all= 6.507793638231878
corrparams= [-0.95703125  0.01226563]
2MSE wt_all= 6.507680719048698
corrparams= [-1.67460938  0.01680469]
2MSE wt_all= 6.508171107990928
corrparams= [-1.6890625   0.01578125]
2MSE wt_all= 6.5082176221778685
corrparams= [-0.32734375  0.00842188]
2MSE wt_all= 6.5078531621401
corrparams= [-1.23515625  0.01332813]
2MSE wt_all= 6.507886217018458
corrparams= [-0.55429688  0.00964844]
2MSE wt

...

2MSE wt_all= 5.699402475993342
corrparams= [-0.01574481  0.56292792]
2MSE wt_all= 5.699309819354775
corrparams= [-0.01478921  0.55955285]
2MSE wt_all= 5.69947597204825
corrparams= [-0.00484588  0.56367656]
2MSE wt_all= 5.699289705855049
corrparams= [0.01032309 0.56242472]
2MSE wt_all= 5.69929429102576
corrparams= [0.00605304 0.56442521]
2MSE wt_all= 5.699318162161381
corrparams= [0.00108138 0.56236335]
2MSE wt_all= 5.699281177935306
corrparams= [-0.01408759  0.5636152 ]
2MSE wt_all= 5.699311321522045
corrparams= [0.00422042 0.56272234]
2MSE wt_all= 5.699279683511866
corrparams= [0.01014768 0.56140913]
2MSE wt_all= 5.699323832063003
corrparams= [-0.00109749  0.5631097 ]
2MSE wt_all= 5.699277898981565
corrparams= [0.00204155 0.56346869]
2MSE wt_all= 5.699282770257489
corrparams= [0.00132142 0.56263969]
2MSE wt_all= 5.699278054973002
corrparams= [-0.00399649  0.56302706]
2MSE wt_all= 5.699279379713312
corrparams= [-0.00194226  0.56295088]
2MSE wt_all= 5.699277512681986
corrparams= [-0.004

2MSE wt_all= 5.569702162208454
corrparams= [0.00307652 0.48250999]
2MSE wt_all= 5.569573460435436
corrparams= [0.01091533 0.48100435]
2MSE wt_all= 5.569567845295112
corrparams= [2.90730659e-04 4.79855816e-01]
2MSE wt_all= 5.569597179575142
corrparams= [0.00238008 0.48184645]
2MSE wt_all= 5.569556742291833
corrparams= [-0.01608334  0.48220355]
2MSE wt_all= 5.569586215904814
corrparams= [0.00416567 0.48130415]
2MSE wt_all= 5.5695555629617
corrparams= [0.01409382 0.48178914]
2MSE wt_all= 5.569573307216746
corrparams= [-0.0021376   0.48146838]
2MSE wt_all= 5.569554028654676
corrparams= [-3.52013939e-04  4.80926082e-01]
2MSE wt_all= 5.569558385201166
corrparams= [0.00169705 0.48161636]
2MSE wt_all= 5.5695543201458335
corrparams= [-0.00460622  0.48178058]
2MSE wt_all= 5.569557328258157
corrparams= [0.00197269 0.48142326]
2MSE wt_all= 5.56955398117149
corrparams= [-0.00186196  0.48127528]
2MSE wt_all= 5.569554474253758
corrparams= [0.0008073  0.48153109]
2MSE wt_all= 5.569553773340332
corrpar

2MSE wt_all= 5.4144979953818915
corrparams= [-0.00715993  0.47407619]
2MSE wt_all= 5.414372896575602
corrparams= [-0.00079409  0.47549728]
2MSE wt_all= 5.4143972377197285
corrparams= [0.00257948 0.47330498]
2MSE wt_all= 5.414372099320813
corrparams= [-0.01465029  0.47338587]
2MSE wt_all= 5.414385200911183
corrparams= [0.00388981 0.47384294]
2MSE wt_all= 5.414369879697681
corrparams= [0.01362923 0.47307173]
2MSE wt_all= 5.41438713844899
corrparams= [-0.00196264  0.47382508]
2MSE wt_all= 5.414369127707822
corrparams= [-0.00065231  0.47436304]
2MSE wt_all= 5.414371806158212
corrparams= [1.55637469e-04 4.74098525e-01]
2MSE wt_all= 5.414369615187623
corrparams= [-0.00569682  0.47408066]
2MSE wt_all= 5.4143716713603975
corrparams= [0.00149316 0.47390237]
2MSE wt_all= 5.414369075330635
corrparams= [-0.00062512  0.47362892]
2MSE wt_all= 5.414369301484676
corrparams= [-4.29931743e-04  4.73746324e-01]
2MSE wt_all= 5.414368952040302
corrparams= [0.00302586 0.47382362]
2MSE wt_all= 5.4143694805767

2MSE wt_all= 3.631372954769286
corrparams= [-0.01144848  0.50359212]
2MSE wt_all= 3.631390494145478
corrparams= [-0.00297279  0.50565698]
2MSE wt_all= 3.6313684768230243
corrparams= [0.01201777 0.50488458]
2MSE wt_all= 3.6313734964393407
corrparams= [-0.00696553  0.50523732]
2MSE wt_all= 3.6313693276070906
corrparams= [-0.01163558  0.5063118 ]
2MSE wt_all= 3.6313767352110595
corrparams= [-0.00163595  0.50501482]
2MSE wt_all= 3.6313686549800135
corrparams= [0.00235679 0.50543449]
2MSE wt_all= 3.631367958168021
corrparams= [0.00701795 0.50553307]
2MSE wt_all= 3.6313693483363183
corrparams= [0.00101995 0.50607665]
2MSE wt_all= 3.6313706305647746
corrparams= [-0.00097197  0.50528028]
2MSE wt_all= 3.6313678704983605
corrparams= [0.00435761 0.50505778]
2MSE wt_all= 3.6313689598109593
corrparams= [-0.00114019  0.50550718]
2MSE wt_all= 3.6313679084239197
corrparams= [-0.00446896  0.50535297]
2MSE wt_all= 3.6313683701878605
corrparams= [0.00065035 0.50541411]
2MSE wt_all= 3.631367798489768
corr

2MSE wt_all= 6.127721577558951
corrparams= [0.01684526 0.50722681]
2MSE wt_all= 6.127837046977432
corrparams= [-0.00617327  0.50432361]
2MSE wt_all= 6.127715168504772
corrparams= [-0.01779334  0.50448716]
2MSE wt_all= 6.127745547229461
corrparams= [0.00103387 0.50502897]
2MSE wt_all= 6.127713599853789
corrparams= [-0.00082894  0.50397946]
2MSE wt_all= 6.12771455429261
corrparams= [0.0063782  0.50468482]
2MSE wt_all= 6.127715099552416
corrparams= [0.00324033 0.50459452]
2MSE wt_all= 6.127711510307704
corrparams= [0.00510314 0.50564402]
2MSE wt_all= 6.127729365999211
corrparams= [0.00065408 0.5043956 ]
2MSE wt_all= 6.127710628488742
corrparams= [0.00286054 0.50396115]
2MSE wt_all= 6.127715668306206
corrparams= [0.00149054 0.50476201]
2MSE wt_all= 6.12771120607096
corrparams= [-0.00109571  0.5045631 ]
2MSE wt_all= 6.127710444780003
corrparams= [-0.00326374  0.50454739]
2MSE wt_all= 6.12771148878009
corrparams= [-0.00193217  0.50419669]
2MSE wt_all= 6.127712285373739
corrparams= [0.0006348

In [ ]:
param100mse=predict_boot(corrparam_list2)
np.sum(param100,axis=0)

In [ ]:
def draw_multi_hist(param_array):
    show(gridplot([param_hist(param_array[:,t]) for t in range(param_array.shape[1])],ncols=int(param_array.shape[1]**.5)))
        
def param_hist(paramvec):
    hist,edges=np.histogram(paramvec, bins=1000)
    p=figure(title='param count={}'.format(paramvec.shape[0]), plot_height=200, plot_width=330)
    p.quad(top=hist/np.size(paramvec), bottom=0, left=edges[:-1], right=edges[1:])
    return p

draw_multi_hist(np.array(corrparam_list2))

In [ ]:
#def PLWLS_bigMin #optimize all n*k+j parameters at once.



In [ ]:
param100mse_2d=param100mse.reshape(param100.shape[0]*param100.shape[1],param100.shape[2])
draw_multi_hist(np.array(param100mse_2d))

In [ ]:
#np.save('corrparam_list2ii500m500',corrparam_list2)
#np.save('param100mse',param100mse)
